In [2]:
import pandas as pd
ch1 = pd.read_csv('./channel_1.dat', names=['Unix', 'Watt'],header=None, delimiter=" ")
print('Done!')

Done!


In [3]:
ch1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21837636 entries, 0 to 21837635
Data columns (total 2 columns):
 #   Column  Dtype
---  ------  -----
 0   Unix    int64
 1   Watt    int64
dtypes: int64(2)
memory usage: 333.2 MB


In [4]:
print(ch1[0:11])
print('1번째')
print(ch1[0:1])
print()
print('21837636번째')
print(ch1[21837635:21837636])

          Unix  Watt
0   1352500095   599
1   1352500101   582
2   1352500107   600
3   1352500113   586
4   1352500120   596
5   1352500132   581
6   1352500138   597
7   1352500144   592
8   1352500150   587
9   1352500156   574
10  1352500168   577
1번째
         Unix  Watt
0  1352500095   599

21837636번째
                Unix  Watt
21837635  1493227960   672


In [5]:
from datetime import datetime
ch1_date = pd.DataFrame(ch1,columns = ['Unix', 'Date', 'Watt'])

ch1_date['Date'] = pd.to_datetime(ch1['Unix'], unit='s')
ch1_date.info()
ch1_date.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21837636 entries, 0 to 21837635
Data columns (total 3 columns):
 #   Column  Dtype         
---  ------  -----         
 0   Unix    int64         
 1   Date    datetime64[ns]
 2   Watt    int64         
dtypes: datetime64[ns](1), int64(2)
memory usage: 499.8 MB


Unix                Date  Watt
0  1352500095 2012-11-09 22:28:15   599
1  1352500101 2012-11-09 22:28:21   582
2  1352500107 2012-11-09 22:28:27   600
3  1352500113 2012-11-09 22:28:33   586
4  1352500120 2012-11-09 22:28:40   596
5  1352500132 2012-11-09 22:28:52   581
6  1352500138 2012-11-09 22:28:58   597
7  1352500144 2012-11-09 22:29:04   592
8  1352500150 2012-11-09 22:29:10   587
9  1352500156 2012-11-09 22:29:16   574

In [6]:
ch1_date[517000:519020]

Unix                Date  Watt
517000  1357551661 2013-01-07 09:41:01   282
517001  1357551667 2013-01-07 09:41:07   282
517002  1357551673 2013-01-07 09:41:13   282
517003  1357551680 2013-01-07 09:41:20   285
517004  1357551686 2013-01-07 09:41:26   284
...            ...                 ...   ...
519015  1357576239 2013-01-07 16:30:39   217
519016  1357576245 2013-01-07 16:30:45   213
519017  1357576252 2013-01-07 16:30:52   217
519018  1357576258 2013-01-07 16:30:58   214
519019  1357576264 2013-01-07 16:31:04   217

[2020 rows x 3 columns]

### 정상 구동 버전 반복을 위한 코드

#### 정보확인을 위한 프린트문 다 지워볼것

In [20]:
import time
import csv

#i = 431368
i = 517000


while(i < 20284836):
    list1 = ch1_date.loc[i].values.tolist()
            
    # Nested List 사용해서 시간 정보만 따로 추출
    date = list1[1]
    y1 = date.year
    M1 = date.month
    d1 = date.day
    H1 = date.hour # 이 H가 있어야 밑에 있는 하루 단위 반복이 돌 변수가 됨.
    n=0
    # 하루 단위 반복
    while(H1 < 24):
        watt_list=[]
        h = date.hour
        # h시와 h+1 시 사이 반복
        while(h < h+1):
            n=n+1
            list2 = ch1_date.loc[i].values.tolist()
            
            date = list2[1]
            watt = list2[2]
            
            y = date.year
            M = date.month
            d = date.day
            h = date.hour
            m = date.minute
            s = date.second
            
            # 확인용 각 변수 출력
            total_date = '{0}년 {1}월 {2}일 - {3}시 {4}분 {5}초'.format(y, M, d, h, m, s)
            print(total_date)
            print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'n >>', n)
            print('칼럼 출력 >>', list2)

            print()
            
            # '시'단위가 바뀌기 전에 값들만 저장 (ex. 1시일 경우 2시가 되기전 데이터들만 저장)
            if(H1==h):
                watt_list.append(watt) # 1시간 동안 6 or 7초 단위로 읽어오는 watt 값들 전부 추가
                i = i+1
                
                
            # 시가 바뀌는 경우 -------------------------------------------------------------------------------------------------
            elif (H1+1==h):
                print('시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
            
            # 시 단위가 순차적으로 넘어가는 것이 아닌 2시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+2==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
                
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 시 단위가 순차적으로 넘어가는 것이 아닌 3시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+3==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -2
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-2)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 시 단위가 순차적으로 넘어가는 것이 아닌 4시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+4==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -3
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-3)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -2
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-2)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 시 단위가 순차적으로 넘어가는 것이 아닌 5시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+5==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
                
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -4
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-4)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -3
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-3)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -2
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-2)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 1 시간치 정리가 끝나고 다음 날로 넘어가는 경우. 따로 설정함.---------------------------------------------------------
            elif(d1+1==d):
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
                d=d-1
                h=h+24
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        

                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)
    
                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
                print('========================================< 하루 끝!! >==================================================')
                print('\n'*4)
                break
                
                
                
            elif (n>590):
                print('데이터 처리 필요!! 반복 루프 강제 종료')
                print('X'*500)
                break
    
        break
        
        
            
    # 하루단위 while 여기서 브레이크를 걸고 다음날로 넘어가도록 해야함.
    
# 전체 While문 종료 지점

2013년 1월 7일 - 9시 41분 1초
d1 >> 7 d >> 7 H1 >> 9 h >> 9   //   i >> 517000 n >> 1
칼럼 출력 >> [1357551661, Timestamp('2013-01-07 09:41:01'), 282]

2013년 1월 7일 - 9시 41분 7초
d1 >> 7 d >> 7 H1 >> 9 h >> 9   //   i >> 517001 n >> 2
칼럼 출력 >> [1357551667, Timestamp('2013-01-07 09:41:07'), 282]

2013년 1월 7일 - 9시 41분 13초
d1 >> 7 d >> 7 H1 >> 9 h >> 9   //   i >> 517002 n >> 3
칼럼 출력 >> [1357551673, Timestamp('2013-01-07 09:41:13'), 282]

2013년 1월 7일 - 9시 41분 20초
d1 >> 7 d >> 7 H1 >> 9 h >> 9   //   i >> 517003 n >> 4
칼럼 출력 >> [1357551680, Timestamp('2013-01-07 09:41:20'), 285]

2013년 1월 7일 - 9시 41분 26초
d1 >> 7 d >> 7 H1 >> 9 h >> 9   //   i >> 517004 n >> 5
칼럼 출력 >> [1357551686, Timestamp('2013-01-07 09:41:26'), 284]

2013년 1월 7일 - 9시 41분 32초
d1 >> 7 d >> 7 H1 >> 9 h >> 9   //   i >> 517005 n >> 6
칼럼 출력 >> [1357551692, Timestamp('2013-01-07 09:41:32'), 279]

2013년 1월 7일 - 9시 41분 38초
d1 >> 7 d >> 7 H1 >> 9 h >> 9   //   i >> 517006 n >> 7
칼럼 출력 >> [1357551698, Timestamp('2013-01-07 09:41:38'), 281]

2

csv 저장 완료!





2013년 1월 7일 - 10시 0분 2초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517179 n >> 1
칼럼 출력 >> [1357552802, Timestamp('2013-01-07 10:00:02'), 287]

2013년 1월 7일 - 10시 0분 8초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517180 n >> 2
칼럼 출력 >> [1357552808, Timestamp('2013-01-07 10:00:08'), 282]

2013년 1월 7일 - 10시 0분 14초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517181 n >> 3
칼럼 출력 >> [1357552814, Timestamp('2013-01-07 10:00:14'), 279]

2013년 1월 7일 - 10시 0분 20초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517182 n >> 4
칼럼 출력 >> [1357552820, Timestamp('2013-01-07 10:00:20'), 287]

2013년 1월 7일 - 10시 0분 26초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517183 n >> 5
칼럼 출력 >> [1357552826, Timestamp('2013-01-07 10:00:26'), 286]

2013년 1월 7일 - 10시 0분 33초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517184 n >> 6
칼럼 출력 >> [1357552833, Timestamp('2013-01-07 10:00:33'), 282]

2013년 1월 7일 - 10시 0분 39초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517185 n >> 7
칼럼 출력 >> [1357552839, Timestamp('

d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517366 n >> 188
칼럼 출력 >> [1357554004, Timestamp('2013-01-07 10:20:04'), 316]

2013년 1월 7일 - 10시 20분 10초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517367 n >> 189
칼럼 출력 >> [1357554010, Timestamp('2013-01-07 10:20:10'), 290]

2013년 1월 7일 - 10시 20분 16초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517368 n >> 190
칼럼 출력 >> [1357554016, Timestamp('2013-01-07 10:20:16'), 291]

2013년 1월 7일 - 10시 20분 22초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517369 n >> 191
칼럼 출력 >> [1357554022, Timestamp('2013-01-07 10:20:22'), 296]

2013년 1월 7일 - 10시 20분 28초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517370 n >> 192
칼럼 출력 >> [1357554028, Timestamp('2013-01-07 10:20:28'), 292]

2013년 1월 7일 - 10시 20분 35초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517371 n >> 193
칼럼 출력 >> [1357554035, Timestamp('2013-01-07 10:20:35'), 289]

2013년 1월 7일 - 10시 20분 41초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517372 n >> 194
칼럼 출력 >> [1357554041, Timestamp('2013-01-07 10:20:41

2013년 1월 7일 - 10시 43분 5초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517577 n >> 399
칼럼 출력 >> [1357555385, Timestamp('2013-01-07 10:43:05'), 365]

2013년 1월 7일 - 10시 43분 11초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517578 n >> 400
칼럼 출력 >> [1357555391, Timestamp('2013-01-07 10:43:11'), 366]

2013년 1월 7일 - 10시 43분 17초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517579 n >> 401
칼럼 출력 >> [1357555397, Timestamp('2013-01-07 10:43:17'), 900]

2013년 1월 7일 - 10시 43분 23초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517580 n >> 402
칼럼 출력 >> [1357555403, Timestamp('2013-01-07 10:43:23'), 361]

2013년 1월 7일 - 10시 43분 30초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517581 n >> 403
칼럼 출력 >> [1357555410, Timestamp('2013-01-07 10:43:30'), 363]

2013년 1월 7일 - 10시 43분 36초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517582 n >> 404
칼럼 출력 >> [1357555416, Timestamp('2013-01-07 10:43:36'), 362]

2013년 1월 7일 - 10시 43분 42초
d1 >> 7 d >> 7 H1 >> 10 h >> 10   //   i >> 517583 n >> 405
칼럼 출력 >> [1357555422, Times

csv 저장 완료!





2013년 1월 7일 - 11시 0분 2초
d1 >> 7 d >> 7 H1 >> 11 h >> 11   //   i >> 517736 n >> 1
칼럼 출력 >> [1357556402, Timestamp('2013-01-07 11:00:02'), 407]

2013년 1월 7일 - 11시 0분 8초
d1 >> 7 d >> 7 H1 >> 11 h >> 11   //   i >> 517737 n >> 2
칼럼 출력 >> [1357556408, Timestamp('2013-01-07 11:00:08'), 411]

2013년 1월 7일 - 11시 0분 15초
d1 >> 7 d >> 7 H1 >> 11 h >> 11   //   i >> 517738 n >> 3
칼럼 출력 >> [1357556415, Timestamp('2013-01-07 11:00:15'), 405]

2013년 1월 7일 - 11시 0분 21초
d1 >> 7 d >> 7 H1 >> 11 h >> 11   //   i >> 517739 n >> 4
칼럼 출력 >> [1357556421, Timestamp('2013-01-07 11:00:21'), 649]

2013년 1월 7일 - 11시 0분 27초
d1 >> 7 d >> 7 H1 >> 11 h >> 11   //   i >> 517740 n >> 5
칼럼 출력 >> [1357556427, Timestamp('2013-01-07 11:00:27'), 411]

2013년 1월 7일 - 11시 0분 39초
d1 >> 7 d >> 7 H1 >> 11 h >> 11   //   i >> 517741 n >> 6
칼럼 출력 >> [1357556439, Timestamp('2013-01-07 11:00:39'), 465]

2013년 1월 7일 - 11시 0분 45초
d1 >> 7 d >> 7 H1 >> 11 h >> 11   //   i >> 517742 n >> 7
칼럼 출력 >> [1357556445, Timestamp('

...

d1 >> 8 d >> 8 H1 >> 4 h >> 4   //   i >> 525763 n >> 413
칼럼 출력 >> [1357620208, Timestamp('2013-01-08 04:43:28'), 176]

2013년 1월 8일 - 4시 43분 34초
d1 >> 8 d >> 8 H1 >> 4 h >> 4   //   i >> 525764 n >> 414
칼럼 출력 >> [1357620214, Timestamp('2013-01-08 04:43:34'), 179]

2013년 1월 8일 - 4시 43분 40초
d1 >> 8 d >> 8 H1 >> 4 h >> 4   //   i >> 525765 n >> 415
칼럼 출력 >> [1357620220, Timestamp('2013-01-08 04:43:40'), 178]

2013년 1월 8일 - 4시 43분 47초
d1 >> 8 d >> 8 H1 >> 4 h >> 4   //   i >> 525766 n >> 416
칼럼 출력 >> [1357620227, Timestamp('2013-01-08 04:43:47'), 177]

2013년 1월 8일 - 4시 43분 53초
d1 >> 8 d >> 8 H1 >> 4 h >> 4   //   i >> 525767 n >> 417
칼럼 출력 >> [1357620233, Timestamp('2013-01-08 04:43:53'), 176]

2013년 1월 8일 - 4시 43분 59초
d1 >> 8 d >> 8 H1 >> 4 h >> 4   //   i >> 525768 n >> 418
칼럼 출력 >> [1357620239, Timestamp('2013-01-08 04:43:59'), 175]

2013년 1월 8일 - 4시 44분 5초
d1 >> 8 d >> 8 H1 >> 4 h >> 4   //   i >> 525769 n >> 419
칼럼 출력 >> [1357620245, Timestamp('2013-01-08 04:44:05'), 179]

2013년 1월 8일

csv 저장 완료!





2013년 1월 8일 - 5시 0분 0초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 525918 n >> 1
칼럼 출력 >> [1357621200, Timestamp('2013-01-08 05:00:00'), 231]

2013년 1월 8일 - 5시 0분 6초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 525919 n >> 2
칼럼 출력 >> [1357621206, Timestamp('2013-01-08 05:00:06'), 227]

2013년 1월 8일 - 5시 0분 12초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 525920 n >> 3
칼럼 출력 >> [1357621212, Timestamp('2013-01-08 05:00:12'), 231]

2013년 1월 8일 - 5시 0분 18초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 525921 n >> 4
칼럼 출력 >> [1357621218, Timestamp('2013-01-08 05:00:18'), 228]

2013년 1월 8일 - 5시 0분 25초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 525922 n >> 5
칼럼 출력 >> [1357621225, Timestamp('2013-01-08 05:00:25'), 229]

2013년 1월 8일 - 5시 0분 31초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 525923 n >> 6
칼럼 출력 >> [1357621231, Timestamp('2013-01-08 05:00:31'), 229]

2013년 1월 8일 - 5시 0분 37초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 525924 n >> 7
칼럼 출력 >> [1357621237, Timestamp('2013-01-08 05:00:37')

d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526125 n >> 208
칼럼 출력 >> [1357622519, Timestamp('2013-01-08 05:21:59'), 176]

2013년 1월 8일 - 5시 22분 5초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526126 n >> 209
칼럼 출력 >> [1357622525, Timestamp('2013-01-08 05:22:05'), 177]

2013년 1월 8일 - 5시 22분 11초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526127 n >> 210
칼럼 출력 >> [1357622531, Timestamp('2013-01-08 05:22:11'), 175]

2013년 1월 8일 - 5시 22분 18초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526128 n >> 211
칼럼 출력 >> [1357622538, Timestamp('2013-01-08 05:22:18'), 174]

2013년 1월 8일 - 5시 22분 24초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526129 n >> 212
칼럼 출력 >> [1357622544, Timestamp('2013-01-08 05:22:24'), 175]

2013년 1월 8일 - 5시 22분 36초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526130 n >> 213
칼럼 출력 >> [1357622556, Timestamp('2013-01-08 05:22:36'), 177]

2013년 1월 8일 - 5시 22분 42초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526131 n >> 214
칼럼 출력 >> [1357622562, Timestamp('2013-01-08 05:22:42'), 175]

2013년 1월 8일

d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526337 n >> 420
칼럼 출력 >> [1357623870, Timestamp('2013-01-08 05:44:30'), 229]

2013년 1월 8일 - 5시 44분 36초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526338 n >> 421
칼럼 출력 >> [1357623876, Timestamp('2013-01-08 05:44:36'), 228]

2013년 1월 8일 - 5시 44분 42초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526339 n >> 422
칼럼 출력 >> [1357623882, Timestamp('2013-01-08 05:44:42'), 229]

2013년 1월 8일 - 5시 44분 48초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526340 n >> 423
칼럼 출력 >> [1357623888, Timestamp('2013-01-08 05:44:48'), 230]

2013년 1월 8일 - 5시 44분 54초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526341 n >> 424
칼럼 출력 >> [1357623894, Timestamp('2013-01-08 05:44:54'), 228]

2013년 1월 8일 - 5시 45분 0초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526342 n >> 425
칼럼 출력 >> [1357623900, Timestamp('2013-01-08 05:45:00'), 230]

2013년 1월 8일 - 5시 45분 13초
d1 >> 8 d >> 8 H1 >> 5 h >> 5   //   i >> 526343 n >> 426
칼럼 출력 >> [1357623913, Timestamp('2013-01-08 05:45:13'), 230]

2013년 1월 8일

KeyboardInterrupt: 

### 전체 범위+ 위의 코드 카피본

In [10]:
import time
import csv

i = 431368


while(i < 20284836):
    list1 = ch1_date.loc[i].values.tolist()
            
    # Nested List 사용해서 시간 정보만 따로 추출
    date = list1[1]
    y1 = date.year
    M1 = date.month
    d1 = date.day
    H1 = date.hour # 이 H가 있어야 밑에 있는 하루 단위 반복이 돌 변수가 됨.
    n=0
    # 하루 단위 반복
    while(H1 < 24):
        watt_list=[]
        h = date.hour
        # h시와 h+1 시 사이 반복
        while(h < h+1):
            n=n+1
            list2 = ch1_date.loc[i].values.tolist()
            
            date = list2[1]
            watt = list2[2]
            
            y = date.year
            M = date.month
            d = date.day
            h = date.hour
            m = date.minute
            s = date.second
            
            # 확인용 각 변수 출력
            total_date = '{0}년 {1}월 {2}일 - {3}시 {4}분 {5}초'.format(y, M, d, h, m, s)
            print(total_date)
            print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'n >>', n)
            print('칼럼 출력 >>', list2)

            print()
            
            # '시'단위가 바뀌기 전에 값들만 저장 (ex. 1시일 경우 2시가 되기전 데이터들만 저장)
            if(H1==h):
                watt_list.append(watt) # 1시간 동안 6 or 7초 단위로 읽어오는 watt 값들 전부 추가
                i = i+1
                
                
            # 시가 바뀌는 경우 -------------------------------------------------------------------------------------------------
            elif (H1+1==h):
                print('시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
            
            # 시 단위가 순차적으로 넘어가는 것이 아닌 2시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+2==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
                
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 시 단위가 순차적으로 넘어가는 것이 아닌 3시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+3==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -2
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-2)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 시 단위가 순차적으로 넘어가는 것이 아닌 4시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+4==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -3
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-3)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -2
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-2)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 시 단위가 순차적으로 넘어가는 것이 아닌 5시간 건너뛰고 점프해버린 경우 ----------------------------------------------
            elif (H1+5==h):
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
                
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -4
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-4)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -3
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-3)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -2
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-2)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                # 점프한 시각 이전까지 Null로 입력 -1
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append('Null')

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
        
            # 1 시간치 정리가 끝나고 다음 날로 넘어가는 경우. 따로 설정함.---------------------------------------------------------
            elif(d1+1==d):
                print('========================================< 1시간치 끝!! >==================================================')
                print('n >>', n)
                print()
                d=d-1
                h=h+24
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        

                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)
    
                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
                print('========================================< 하루 끝!! >==================================================')
                print('\n'*4)
                break
                
                
                
            elif (n>590):
                print('데이터 처리 필요!! 반복 루프 강제 종료')
                print('X'*500)
                break
    
        break
        
        
            
    # 하루단위 while 여기서 브레이크를 걸고 다음날로 넘어가도록 해야함.
    
# 전체 While문 종료 지점

2013년 1월 1일 - 0시 0분 1초
d1 >> 1 d >> 1 i >> 431368
칼럼 출력 >> [1356998401, Timestamp('2013-01-01 00:00:01'), 499]

2013년 1월 1일 - 0시 0분 7초
d1 >> 1 d >> 1 i >> 431369
칼럼 출력 >> [1356998407, Timestamp('2013-01-01 00:00:07'), 500]

2013년 1월 1일 - 0시 0분 13초
d1 >> 1 d >> 1 i >> 431370
칼럼 출력 >> [1356998413, Timestamp('2013-01-01 00:00:13'), 515]

2013년 1월 1일 - 0시 0분 19초
d1 >> 1 d >> 1 i >> 431371
칼럼 출력 >> [1356998419, Timestamp('2013-01-01 00:00:19'), 522]

2013년 1월 1일 - 0시 0분 26초
d1 >> 1 d >> 1 i >> 431372
칼럼 출력 >> [1356998426, Timestamp('2013-01-01 00:00:26'), 508]

2013년 1월 1일 - 0시 0분 32초
d1 >> 1 d >> 1 i >> 431373
칼럼 출력 >> [1356998432, Timestamp('2013-01-01 00:00:32'), 502]

2013년 1월 1일 - 0시 0분 38초
d1 >> 1 d >> 1 i >> 431374
칼럼 출력 >> [1356998438, Timestamp('2013-01-01 00:00:38'), 507]

2013년 1월 1일 - 0시 0분 44초
d1 >> 1 d >> 1 i >> 431375
칼럼 출력 >> [1356998444, Timestamp('2013-01-01 00:00:44'), 508]

2013년 1월 1일 - 0시 0분 50초
d1 >> 1 d >> 1 i >> 431376
칼럼 출력 >> [1356998450, Timestamp('2013-01-01 00:

2013년 1월 1일 - 0시 35분 45초
d1 >> 1 d >> 1 i >> 431694
칼럼 출력 >> [1357000545, Timestamp('2013-01-01 00:35:45'), 402]

2013년 1월 1일 - 0시 35분 52초
d1 >> 1 d >> 1 i >> 431695
칼럼 출력 >> [1357000552, Timestamp('2013-01-01 00:35:52'), 393]

2013년 1월 1일 - 0시 35분 58초
d1 >> 1 d >> 1 i >> 431696
칼럼 출력 >> [1357000558, Timestamp('2013-01-01 00:35:58'), 398]

2013년 1월 1일 - 0시 36분 4초
d1 >> 1 d >> 1 i >> 431697
칼럼 출력 >> [1357000564, Timestamp('2013-01-01 00:36:04'), 399]

2013년 1월 1일 - 0시 36분 10초
d1 >> 1 d >> 1 i >> 431698
칼럼 출력 >> [1357000570, Timestamp('2013-01-01 00:36:10'), 400]

2013년 1월 1일 - 0시 36분 16초
d1 >> 1 d >> 1 i >> 431699
칼럼 출력 >> [1357000576, Timestamp('2013-01-01 00:36:16'), 405]

2013년 1월 1일 - 0시 36분 22초
d1 >> 1 d >> 1 i >> 431700
칼럼 출력 >> [1357000582, Timestamp('2013-01-01 00:36:22'), 420]

2013년 1월 1일 - 0시 36분 28초
d1 >> 1 d >> 1 i >> 431701
칼럼 출력 >> [1357000588, Timestamp('2013-01-01 00:36:28'), 463]

2013년 1월 1일 - 0시 36분 35초
d1 >> 1 d >> 1 i >> 431702
칼럼 출력 >> [1357000595, Timestamp('2013

csv 저장 완료!





2013년 1월 1일 - 1시 0분 5초
d1 >> 1 d >> 1 i >> 431925
칼럼 출력 >> [1357002005, Timestamp('2013-01-01 01:00:05'), 2475]

2013년 1월 1일 - 1시 0분 11초
d1 >> 1 d >> 1 i >> 431926
칼럼 출력 >> [1357002011, Timestamp('2013-01-01 01:00:11'), 2481]

2013년 1월 1일 - 1시 0분 17초
d1 >> 1 d >> 1 i >> 431927
칼럼 출력 >> [1357002017, Timestamp('2013-01-01 01:00:17'), 2477]

2013년 1월 1일 - 1시 0분 22초
d1 >> 1 d >> 1 i >> 431928
칼럼 출력 >> [1357002022, Timestamp('2013-01-01 01:00:22'), 2476]

2013년 1월 1일 - 1시 0분 28초
d1 >> 1 d >> 1 i >> 431929
칼럼 출력 >> [1357002028, Timestamp('2013-01-01 01:00:28'), 2477]

2013년 1월 1일 - 1시 0분 34초
d1 >> 1 d >> 1 i >> 431930
칼럼 출력 >> [1357002034, Timestamp('2013-01-01 01:00:34'), 2473]

2013년 1월 1일 - 1시 0분 40초
d1 >> 1 d >> 1 i >> 431931
칼럼 출력 >> [1357002040, Timestamp('2013-01-01 01:00:40'), 2480]

2013년 1월 1일 - 1시 0분 46초
d1 >> 1 d >> 1 i >> 431932
칼럼 출력 >> [1357002046, Timestamp('2013-01-01 01:00:46'), 2475]

2013년 1월 1일 - 1시 0분 52초
d1 >> 1 d >> 1 i >> 431933
칼럼 출력 >> [1357002052, 

d1 >> 1 d >> 1 i >> 432246
칼럼 출력 >> [1357004006, Timestamp('2013-01-01 01:33:26'), 352]

2013년 1월 1일 - 1시 33분 32초
d1 >> 1 d >> 1 i >> 432247
칼럼 출력 >> [1357004012, Timestamp('2013-01-01 01:33:32'), 356]

2013년 1월 1일 - 1시 33분 38초
d1 >> 1 d >> 1 i >> 432248
칼럼 출력 >> [1357004018, Timestamp('2013-01-01 01:33:38'), 357]

2013년 1월 1일 - 1시 33분 44초
d1 >> 1 d >> 1 i >> 432249
칼럼 출력 >> [1357004024, Timestamp('2013-01-01 01:33:44'), 357]

2013년 1월 1일 - 1시 33분 50초
d1 >> 1 d >> 1 i >> 432250
칼럼 출력 >> [1357004030, Timestamp('2013-01-01 01:33:50'), 352]

2013년 1월 1일 - 1시 33분 56초
d1 >> 1 d >> 1 i >> 432251
칼럼 출력 >> [1357004036, Timestamp('2013-01-01 01:33:56'), 352]

2013년 1월 1일 - 1시 34분 2초
d1 >> 1 d >> 1 i >> 432252
칼럼 출력 >> [1357004042, Timestamp('2013-01-01 01:34:02'), 354]

2013년 1월 1일 - 1시 34분 8초
d1 >> 1 d >> 1 i >> 432253
칼럼 출력 >> [1357004048, Timestamp('2013-01-01 01:34:08'), 352]

2013년 1월 1일 - 1시 34분 15초
d1 >> 1 d >> 1 i >> 432254
칼럼 출력 >> [1357004055, Timestamp('2013-01-01 01:34:15'), 354]

2

csv 저장 완료!





2013년 1월 1일 - 2시 0분 4초
d1 >> 1 d >> 1 i >> 432490
칼럼 출력 >> [1357005604, Timestamp('2013-01-01 02:00:04'), 2439]

2013년 1월 1일 - 2시 0분 9초
d1 >> 1 d >> 1 i >> 432491
칼럼 출력 >> [1357005609, Timestamp('2013-01-01 02:00:09'), 2429]

2013년 1월 1일 - 2시 0분 15초
d1 >> 1 d >> 1 i >> 432492
칼럼 출력 >> [1357005615, Timestamp('2013-01-01 02:00:15'), 2435]

2013년 1월 1일 - 2시 0분 21초
d1 >> 1 d >> 1 i >> 432493
칼럼 출력 >> [1357005621, Timestamp('2013-01-01 02:00:21'), 2429]

2013년 1월 1일 - 2시 0분 27초
d1 >> 1 d >> 1 i >> 432494
칼럼 출력 >> [1357005627, Timestamp('2013-01-01 02:00:27'), 2428]

2013년 1월 1일 - 2시 0분 33초
d1 >> 1 d >> 1 i >> 432495
칼럼 출력 >> [1357005633, Timestamp('2013-01-01 02:00:33'), 2433]

2013년 1월 1일 - 2시 0분 45초
d1 >> 1 d >> 1 i >> 432496
칼럼 출력 >> [1357005645, Timestamp('2013-01-01 02:00:45'), 2427]

2013년 1월 1일 - 2시 0분 51초
d1 >> 1 d >> 1 i >> 432497
칼럼 출력 >> [1357005651, Timestamp('2013-01-01 02:00:51'), 2424]

2013년 1월 1일 - 2시 0분 57초
d1 >> 1 d >> 1 i >> 432498
칼럼 출력 >> [1357005657, T

...

csv 저장 완료!





2013년 1월 2일 - 2시 0분 5초
d1 >> 2 d >> 2 i >> 445833
칼럼 출력 >> [1357092005, Timestamp('2013-01-02 02:00:05'), 228]

2013년 1월 2일 - 2시 0분 11초
d1 >> 2 d >> 2 i >> 445834
칼럼 출력 >> [1357092011, Timestamp('2013-01-02 02:00:11'), 226]

2013년 1월 2일 - 2시 0분 17초
d1 >> 2 d >> 2 i >> 445835
칼럼 출력 >> [1357092017, Timestamp('2013-01-02 02:00:17'), 226]

2013년 1월 2일 - 2시 0분 23초
d1 >> 2 d >> 2 i >> 445836
칼럼 출력 >> [1357092023, Timestamp('2013-01-02 02:00:23'), 226]

2013년 1월 2일 - 2시 0분 30초
d1 >> 2 d >> 2 i >> 445837
칼럼 출력 >> [1357092030, Timestamp('2013-01-02 02:00:30'), 226]

2013년 1월 2일 - 2시 0분 42초
d1 >> 2 d >> 2 i >> 445838
칼럼 출력 >> [1357092042, Timestamp('2013-01-02 02:00:42'), 226]

2013년 1월 2일 - 2시 0분 48초
d1 >> 2 d >> 2 i >> 445839
칼럼 출력 >> [1357092048, Timestamp('2013-01-02 02:00:48'), 228]

2013년 1월 2일 - 2시 0분 54초
d1 >> 2 d >> 2 i >> 445840
칼럼 출력 >> [1357092054, Timestamp('2013-01-02 02:00:54'), 229]

2013년 1월 2일 - 2시 1분 0초
d1 >> 2 d >> 2 i >> 445841
칼럼 출력 >> [1357092060, Timestamp


2013년 1월 2일 - 2시 33분 4초
d1 >> 2 d >> 2 i >> 446140
칼럼 출력 >> [1357093984, Timestamp('2013-01-02 02:33:04'), 165]

2013년 1월 2일 - 2시 33분 16초
d1 >> 2 d >> 2 i >> 446141
칼럼 출력 >> [1357093996, Timestamp('2013-01-02 02:33:16'), 165]

2013년 1월 2일 - 2시 33분 22초
d1 >> 2 d >> 2 i >> 446142
칼럼 출력 >> [1357094002, Timestamp('2013-01-02 02:33:22'), 165]

2013년 1월 2일 - 2시 33분 29초
d1 >> 2 d >> 2 i >> 446143
칼럼 출력 >> [1357094009, Timestamp('2013-01-02 02:33:29'), 169]

2013년 1월 2일 - 2시 33분 35초
d1 >> 2 d >> 2 i >> 446144
칼럼 출력 >> [1357094015, Timestamp('2013-01-02 02:33:35'), 165]

2013년 1월 2일 - 2시 33분 41초
d1 >> 2 d >> 2 i >> 446145
칼럼 출력 >> [1357094021, Timestamp('2013-01-02 02:33:41'), 165]

2013년 1월 2일 - 2시 33분 47초
d1 >> 2 d >> 2 i >> 446146
칼럼 출력 >> [1357094027, Timestamp('2013-01-02 02:33:47'), 168]

2013년 1월 2일 - 2시 33분 53초
d1 >> 2 d >> 2 i >> 446147
칼럼 출력 >> [1357094033, Timestamp('2013-01-02 02:33:53'), 166]

2013년 1월 2일 - 2시 33분 59초
d1 >> 2 d >> 2 i >> 446148
칼럼 출력 >> [1357094039, Timestamp('201

csv 저장 완료!





2013년 1월 2일 - 3시 0분 0초
d1 >> 2 d >> 2 i >> 446392
칼럼 출력 >> [1357095600, Timestamp('2013-01-02 03:00:00'), 166]

2013년 1월 2일 - 3시 0분 6초
d1 >> 2 d >> 2 i >> 446393
칼럼 출력 >> [1357095606, Timestamp('2013-01-02 03:00:06'), 165]

2013년 1월 2일 - 3시 0분 12초
d1 >> 2 d >> 2 i >> 446394
칼럼 출력 >> [1357095612, Timestamp('2013-01-02 03:00:12'), 165]

2013년 1월 2일 - 3시 0분 18초
d1 >> 2 d >> 2 i >> 446395
칼럼 출력 >> [1357095618, Timestamp('2013-01-02 03:00:18'), 167]

2013년 1월 2일 - 3시 0분 24초
d1 >> 2 d >> 2 i >> 446396
칼럼 출력 >> [1357095624, Timestamp('2013-01-02 03:00:24'), 166]

2013년 1월 2일 - 3시 0분 30초
d1 >> 2 d >> 2 i >> 446397
칼럼 출력 >> [1357095630, Timestamp('2013-01-02 03:00:30'), 165]

2013년 1월 2일 - 3시 0분 37초
d1 >> 2 d >> 2 i >> 446398
칼럼 출력 >> [1357095637, Timestamp('2013-01-02 03:00:37'), 166]

2013년 1월 2일 - 3시 0분 43초
d1 >> 2 d >> 2 i >> 446399
칼럼 출력 >> [1357095643, Timestamp('2013-01-02 03:00:43'), 166]

2013년 1월 2일 - 3시 0분 49초
d1 >> 2 d >> 2 i >> 446400
칼럼 출력 >> [1357095649, Timestamp

칼럼 출력 >> [1357097648, Timestamp('2013-01-02 03:34:08'), 165]

2013년 1월 2일 - 3시 34분 15초
d1 >> 2 d >> 2 i >> 446717
칼럼 출력 >> [1357097655, Timestamp('2013-01-02 03:34:15'), 167]

2013년 1월 2일 - 3시 34분 21초
d1 >> 2 d >> 2 i >> 446718
칼럼 출력 >> [1357097661, Timestamp('2013-01-02 03:34:21'), 164]

2013년 1월 2일 - 3시 34분 27초
d1 >> 2 d >> 2 i >> 446719
칼럼 출력 >> [1357097667, Timestamp('2013-01-02 03:34:27'), 169]

2013년 1월 2일 - 3시 34분 33초
d1 >> 2 d >> 2 i >> 446720
칼럼 출력 >> [1357097673, Timestamp('2013-01-02 03:34:33'), 165]

2013년 1월 2일 - 3시 34분 39초
d1 >> 2 d >> 2 i >> 446721
칼럼 출력 >> [1357097679, Timestamp('2013-01-02 03:34:39'), 165]

2013년 1월 2일 - 3시 34분 45초
d1 >> 2 d >> 2 i >> 446722
칼럼 출력 >> [1357097685, Timestamp('2013-01-02 03:34:45'), 164]

2013년 1월 2일 - 3시 34분 52초
d1 >> 2 d >> 2 i >> 446723
칼럼 출력 >> [1357097692, Timestamp('2013-01-02 03:34:52'), 165]

2013년 1월 2일 - 3시 34분 58초
d1 >> 2 d >> 2 i >> 446724
칼럼 출력 >> [1357097698, Timestamp('2013-01-02 03:34:58'), 167]

2013년 1월 2일 - 3시 35분 4초
d1

KeyboardInterrupt: 